In [1]:
import numpy as np
import tensorflow as tf
import matplotlib.pyplot as plt

/opt/conda/lib/python3.10/site-packages/tensorflow_io/python/ops/__init__.py:98: UserWarning: unable to load libtensorflow_io_plugins.so: unable to open file: libtensorflow_io_plugins.so, from paths: ['/opt/conda/lib/python3.10/site-packages/tensorflow_io/python/ops/libtensorflow_io_plugins.so']
caused by: ['/opt/conda/lib/python3.10/site-packages/tensorflow_io/python/ops/libtensorflow_io_plugins.so: undefined symbol: _ZN3tsl6StatusC1EN10tensorflow5error4CodeESt17basic_string_viewIcSt11char_traitsIcEENS_14SourceLocationE']
  warnings.warn(f"unable to load libtensorflow_io_plugins.so: {e}")
/opt/conda/lib/python3.10/site-packages/tensorflow_io/python/ops/__init__.py:104: UserWarning: file system plugins are not loaded: unable to open file: libtensorflow_io.so, from paths: ['/opt/conda/lib/python3.10/site-packages/tensorflow_io/python/ops/libtensorflow_io.so']
caused by: ['/opt/conda/lib/python3.10/site-packages/tensorflow_io/python/ops/libtensorflow_io.so: undefined symbol: _ZTVN10tenso

In [29]:
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Conv2D, MaxPooling2D, UpSampling2D, Concatenate


input_shape = (572, 572, 1)  # Example input shape
num_classes = 10  # Example number of classes


# Contracting Path
inputs = Input(input_shape, name='input')
conv1 = Conv2D(64, 3, activation='relu', name='conv11')(inputs)
conv1 = Conv2D(64, 3, activation='relu', name='conv12')(conv1)
pool1 = MaxPooling2D(pool_size=2, name='pool1')(conv1)

conv2 = Conv2D(128, 3, activation='relu', name='conv21')(pool1)
conv2 = Conv2D(128, 3, activation='relu', name='conv22')(conv2)
pool2 = MaxPooling2D(pool_size=2, name='pool2')(conv2)

conv3 = Conv2D(256, 3, activation='relu', name='conv31')(pool2)
conv3 = Conv2D(256, 3, activation='relu', name='conv32')(conv3)
pool3 = MaxPooling2D(pool_size=2, name='pool3')(conv3)

conv4 = Conv2D(512, 3, activation='relu', name='conv41')(pool3)
conv4 = Conv2D(512, 3, activation='relu', name='conv42')(conv4)
pool4 = MaxPooling2D(pool_size=2, name='pool4')(conv4)

conv5 = Conv2D(1024, 3, activation='relu', name='conv51')(pool4)
conv5 = Conv2D(1024, 3, activation='relu', name='conv52')(conv5)


# Expanding Path
up6 = Conv2D(512, 2, activation='relu', padding='same', name='up_conv6')(UpSampling2D(size=2)(conv5))
shape = up6.shape
cropped_conv4 = conv4[:, :shape[1], :shape[2], :]
merge6 = Concatenate(axis=3)([cropped_conv4, up6])
conv6 = Conv2D(512, 3, activation='relu', name='conv61')(merge6)
conv6 = Conv2D(512, 3, activation='relu', name='conv62')(conv6)

up7 = Conv2D(256, 2, activation='relu', padding='same', name='up_conv7')(UpSampling2D(size=2)(conv6))
shape = up7.shape
cropped_conv3 = conv3[:, :shape[1], :shape[2], :]
merge7 = Concatenate(axis=3)([cropped_conv3, up7])
conv7 = Conv2D(256, 3, activation='relu', name='conv71')(merge7)
conv7 = Conv2D(256, 3, activation='relu', name='conv72')(conv7)

up8 = Conv2D(128, 2, activation='relu', padding='same', name='up_conv8')(UpSampling2D(size=2)(conv7))
shape = up8.shape
cropped_conv2 = conv2[:, :shape[1], :shape[2], :]
merge8 = Concatenate(axis=3)([cropped_conv2, up8])
conv8 = Conv2D(128, 3, activation='relu', name='conv81')(merge8)
conv8 = Conv2D(128, 3, activation='relu', name='conv82')(conv8)

up9 = Conv2D(64, 2, activation='relu', padding='same', name='up_conv9')(UpSampling2D(size=2)(conv8))
shape = up9.shape
cropped_conv1 = conv1[:, :shape[1], :shape[2], :]
merge9 = Concatenate(axis=3)([cropped_conv1, up9])
conv9 = Conv2D(64, 3, activation='relu', name='conv91')(merge9)
conv9 = Conv2D(64, 3, activation='relu', name='conv92')(conv9)


# Output layer
outputs = Conv2D(num_classes, 1, activation='softmax', name='output')(conv9)

# Create the model
model = Model(inputs, outputs, name='UNet')

# Print the summary of the model
model.summary()

Model: "UNet"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input (InputLayer)             [(None, 572, 572, 1  0           []                               
                                )]                                                                
                                                                                                  
 conv11 (Conv2D)                (None, 570, 570, 64  640         ['input[0][0]']                  
                                )                                                                 
                                                                                                  
 conv12 (Conv2D)                (None, 568, 568, 64  36928       ['conv11[0][0]']                 
                                )                                                              

In [30]:
# Plot the model
tf.keras.utils.plot_model(
    model,
    to_file="UNet.png",
    show_shapes=True,
    show_dtype=False,
    show_layer_names=True,
    rankdir="TB",
    expand_nested=False,
    dpi=1200,
    layer_range=None,
    show_layer_activations=True,
    show_trainable=False,
)